In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib import colors as mcolors

import trimesh

from concurrent.futures import ThreadPoolExecutor

import scipy.sparse as sp
from scipy.spatial import cKDTree

from sklearn.cluster import SpectralClustering

In [2]:
import sys
import os

# Get the absolute path to the src directory and add it to sys.path
src_path = os.path.abspath(os.path.join('..', 'src'))
if src_path not in sys.path:
    sys.path.append(src_path)

In [3]:
from affinity_matrix_construction import AffinityMatrixConstruction
from garland_heckbert_algorithm import SimplifyMesh3D

In [4]:
# CONSTANTS:
MODELS_FOLDER_PATH = './../data/segmentation_data/off/'
BENCHMARK_FOLDER_PATH = './../data/segmentation_data/seg/Benchmark/'
RANDOM_STATE = 37
PAPER_COEFFICIENT = 0.005
verbose = True

In [5]:
def colour_detailed_clusters(mesh, cluster_labels, detailed_clusters, default_color=(0.5, 0.5, 0.5, 1.0)):
    """
    Colour the mesh segmentation highlighting only the detailed clusters.

    Parameters:
    - mesh (trimesh.Trimesh): The mesh object.
    - cluster_labels (np.ndarray): Cluster labels for each face.
    - detailed_clusters (set): Set of cluster IDs to highlight.
    - default_color (tuple): RGBA color for non-detailed clusters.

    Returns:
    - mesh (trimesh.Trimesh): Mesh with colored faces.
    """
    # Generate distinct colors for detailed clusters
    def generate_distinct_colors(num_colors):
        # Use evenly spaced hues in HSV color space
        hues = np.linspace(0, 1, num_colors, endpoint=False)
        rgb_colors = [mcolors.hsv_to_rgb((h, 1, 1)) for h in hues]
        rgba_colors = np.array([np.append(color, 1.0) for color in rgb_colors])  # Add alpha channel
        return rgba_colors

    # Assign a distinct color to each detailed cluster
    detailed_clusters = sorted(detailed_clusters)  # Ensure consistent order
    colors = generate_distinct_colors(len(detailed_clusters))
    cluster_to_color = {cluster: colors[i] for i, cluster in enumerate(detailed_clusters)}

    # Default face color (e.g., gray)
    default_rgba = np.array(default_color)

    # Create face colors array
    face_colors = np.zeros((len(cluster_labels), 4))  # RGBA for each face
    for i, label in enumerate(cluster_labels):
        if label in cluster_to_color:
            face_colors[i] = cluster_to_color[label]  # Assign cluster color
        else:
            face_colors[i] = default_rgba  # Assign default color

    # Assign colors to mesh faces
    mesh.visual.face_colors = (face_colors * 255).astype(np.uint8)

    return mesh

In [6]:
mesh = trimesh.load(MODELS_FOLDER_PATH + "1.off")

In [7]:
mesh = mesh.process(validate=True)
mesh.fix_normals(multibody=True)

In [8]:
mesh.show()

For this model it takes around 8 minutes to compute on my PC so that is why I saved the sparse matrix in a file.

In [9]:
matrix_name = "mesh1_affinity_matrix.npz"
if os.path.isfile(matrix_name):
    affinity_matrix = sp.load_npz(matrix_name)
else:
    construct = AffinityMatrixConstruction(0.0045, True, 'approximate')
    affinity_matrix = construct.construct_affinity_matrix(mesh)
    sp.save_npz(matrix_name, affinity_matrix)

I though why not use the parameters which worked for the octopus best (even though the mesh is different, and the cluster count is different).

I chose 23 clusters so we can capture small bits of the body. There is an interesting bug when more clusters are wanted that some points faces which are divided by other clusters end up in the same cluster. I will have to look into it later on.
Another interesting problem is defining how many clusters one will need in order to obtain a good segmentation.

In [85]:
sc = SpectralClustering(n_clusters=23, affinity='precomputed', random_state=RANDOM_STATE, assign_labels='cluster_qr', eigen_solver='amg')

In [86]:
cluster_labels = sc.fit_predict(affinity_matrix)

In [87]:
colour_detailed_clusters(mesh, cluster_labels, cluster_labels).show(smooth=False)

# Heuristic Approaches to Identify High-Detail Clusters

The **dihedral angle** between two adjacent faces $A$ and $B$ is defined as:
\begin{equation*}
\theta = \arccos\left(\frac{\mathbf{n}_A \cdot \mathbf{n}_B}{\|\mathbf{n}_A\| \|\mathbf{n}_B\|}\right)
\end{equation*}
Where:
- $\mathbf{n}_A, \mathbf{n}_B$: Normal vectors of the faces.
- $\theta$: The angle in radians, measuring the "bend" between the two faces.

**Classification of Angles**
- **Concave Regions**:
  - $\theta > 90^\circ$ or $\cos(\theta) < 0$ indicate sharp inward bends.
- **Convex and Flat Regions**:
  - Not very interesting to us as the dihedral angles in a mesh are mostly of these types.


Now I will also consider the ratio of concave angles w.r.t. all angles in the submesh, but as we see for the current mesh as it is already low poly, there are very few concave angles.

In [88]:
def compute_concave_edge_ratio(submesh, threshold=np.radians(120)):
    """
    Compute the proportion of concave edges in a submesh.

    Parameters:
    - submesh: trimesh.Trimesh
        A submesh representing a cluster.
    - threshold: float
        The dihedral angle threshold (in radians).
    - scale_factor: float
        Factor to scale the threshold based on density.

    Returns:
    - concave_ratio: float
        Ratio of concave edges in the submesh.
    """
    face_normals = submesh.face_normals
    total_edges = len(submesh.edges_unique)
    if total_edges == 0:
        return 0  # Avoid division by zero for small or degenerate clusters

    concave_edges = 0
    for adjacency in submesh.face_adjacency:
        if adjacency[0] != -1 and adjacency[1] != -1:  # Valid face adjacency
            normal1 = face_normals[adjacency[0]]
            normal2 = face_normals[adjacency[1]]
            cos_theta = np.dot(normal1, normal2) / (np.linalg.norm(normal1) * np.linalg.norm(normal2))
            cos_theta = np.clip(cos_theta, -1, 1)  # Avoid numerical issues
            angle = np.arccos(cos_theta)

            if angle > threshold:
                concave_edges += 1

    concave_ratio = concave_edges / total_edges
    return concave_ratio


In [89]:
def identify_high_detail_clusters_by_ratio(mesh, cluster_labels, threshold=np.radians(120), min_concave_ratio=0.1):
    """
    Identify high-detail clusters based on the proportion of concave edges.

    Parameters:
    - mesh: trimesh.Trimesh
        The input mesh.
    - cluster_labels: numpy.ndarray
        Cluster labels for each face.
    - min_concave_ratio: float
        Minimum ratio of concave edges required to classify a cluster as high-detail.

    Returns:
    - high_detail_clusters: set
        Indices of clusters identified as high-detail.
    """
    def partition_mesh_by_clusters(mesh, cluster_labels):
        unique_clusters = np.unique(cluster_labels)
        submeshes = {}

        for cluster in unique_clusters:
            # Get faces belonging to the current cluster
            cluster_faces = np.where(cluster_labels == cluster)[0]
            
            # Create a submesh for the cluster
            submesh = mesh.submesh([cluster_faces], append=True)
            submeshes[cluster] = submesh
            
        return submeshes
    
    # Partition the mesh into submeshes
    submeshes = partition_mesh_by_clusters(mesh, cluster_labels)

    def process_cluster(cluster):
        submesh = submeshes[cluster]
        concave_ratio = compute_concave_edge_ratio(submesh, threshold)
        return cluster if concave_ratio > min_concave_ratio else None

    # Use ThreadPoolExecutor for parallel processing
    high_detail_clusters = set()
    with ThreadPoolExecutor() as executor:
        results = executor.map(process_cluster, submeshes.keys())
        for cluster in results:
            if cluster is not None:
                high_detail_clusters.add(cluster)

    return high_detail_clusters


In [90]:
# Identify high-detail clusters based on concave edge ratio
high_detail_clusters = identify_high_detail_clusters_by_ratio(mesh, cluster_labels, threshold=np.radians(90), min_concave_ratio=0.0)

# Color and visualize high-detail clusters
colored_mesh = colour_detailed_clusters(mesh, cluster_labels, high_detail_clusters)
colored_mesh.show()

In [91]:
simplify = SimplifyMesh3D()

In [92]:
dir(simplify)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getstate__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'add_boundary_quadrics',
 'clean',
 'compute_pair_cost',
 'compute_vertex_Q',
 'face_id_counter',
 'faces',
 'generate_perpendicular_plane',
 'initial_compute_error_quadrics',
 'is_boundary_edge',
 'load_file',
 'load_from_blender',
 'load_into_blender',
 'load_mesh',
 'mark_high_detail_vertices',
 'optimal_positions',
 'output_file',
 'output_mesh',
 'pair_costs',
 'pairs',
 'penalty_weight',
 'prevent_mesh_inversion',
 'print_mesh_stats',
 'select_valid_pairs',
 'simplification_ratio',
 'simplify',
 'simplify_obj',
 'simplify_obj_from_blender',
 'simplify_obj_from_file',
 'simplify_obj_penalize_clusters

In [93]:
mesh_res = simplify.simplify_obj_penalize_clusters(mesh, cluster_labels, high_detail_clusters, 10)

Loaded 3D model.
Selecting the initial valid to contract pairs is done!
0.00% done with 2353 vertices remaining to be removed.
4.25% done with 2253 vertices remaining to be removed.
8.50% done with 2153 vertices remaining to be removed.
12.75% done with 2053 vertices remaining to be removed.
17.00% done with 1953 vertices remaining to be removed.
21.25% done with 1853 vertices remaining to be removed.
25.50% done with 1753 vertices remaining to be removed.
29.75% done with 1653 vertices remaining to be removed.
34.00% done with 1553 vertices remaining to be removed.
38.25% done with 1453 vertices remaining to be removed.
42.50% done with 1353 vertices remaining to be removed.
46.75% done with 1253 vertices remaining to be removed.
51.00% done with 1153 vertices remaining to be removed.
55.25% done with 1053 vertices remaining to be removed.
59.50% done with 953 vertices remaining to be removed.
63.75% done with 853 vertices remaining to be removed.
68.00% done with 753 vertices remaini

In [94]:
mesh_res.show()

In [95]:
mesh_res_no_penalty = simplify.simplify_obj(mesh)

Loaded 3D model.
Selecting the initial valid to contract pairs is done!
0.00% done with 2353 vertices remaining to be removed.
4.25% done with 2253 vertices remaining to be removed.
8.50% done with 2153 vertices remaining to be removed.
12.75% done with 2053 vertices remaining to be removed.
17.00% done with 1953 vertices remaining to be removed.
21.25% done with 1853 vertices remaining to be removed.
25.50% done with 1753 vertices remaining to be removed.
29.75% done with 1653 vertices remaining to be removed.
34.00% done with 1553 vertices remaining to be removed.
38.25% done with 1453 vertices remaining to be removed.
42.50% done with 1353 vertices remaining to be removed.
46.75% done with 1253 vertices remaining to be removed.
51.00% done with 1153 vertices remaining to be removed.
55.25% done with 1053 vertices remaining to be removed.
59.50% done with 953 vertices remaining to be removed.
63.75% done with 853 vertices remaining to be removed.
68.00% done with 753 vertices remaini

In [96]:
mesh_res_no_penalty.show()

I would like to use a visual fidelity test w.r.t. the original mesh if there is some improvement over simplifying without penalizing detailed clusters:

Remember the metric described in Section 6.1 of the paper titled "Surface Simplification Using Quadric Error Metrics" by Michael Garland and Paul S. Heckbert?
It measures the quality of approximations by calculating the average squared distance between the original model and its simplified version. This metric is closely related to what is known as the *mean squared error* but applied to 3D meshes.
The error metric $E_i$ is defined as follows:

\begin{equation*}
E_i = \frac{1}{|X_n| + |X_i|} \left( \sum_{v \in X_n} d^2(v, M_i) + \sum_{v \in X_i} d^2(v, M_n) \right)
\end{equation*}

Where:
- $X_n$ is a set of points sampled on the original model $M_n$.
- $X_i$ is a set of points sampled on the simplified model $M_i$.
- $d(v, M)$ is the minimum distance from a point $v$ to the closest face of the model $M$.

This metric averages the squared distances from the points on the original mesh to the simplified mesh and vice versa.



In [97]:
SAMPLE_SIZE = 10000

In [98]:
def mesh_simplification_error(mesh1, mesh2):
    """
    Calculate the error metric as described in Section 6.1.
    
    Parameters:
    mesh1 (trimesh.Trimesh): The first mesh, typically the original mesh.
    mesh2 (trimesh.Trimesh): The second mesh, typically the simplified mesh.

    Returns:
    float: The Section 6.1 defined metric distnace between the two meshes.
    """
    points1 = mesh1.sample(SAMPLE_SIZE)
    points2 = mesh2.sample(SAMPLE_SIZE)
    
    tree1 = cKDTree(points1)
    tree2 = cKDTree(points2)
    
    # Sum of squared distances from original mesh points to simplified mesh
    distances_1_to_2, _ = tree2.query(points1, k=1)
    error_1_to_2 = np.sum(distances_1_to_2**2)
    
    # Sum of squared distances from simplified mesh points to original mesh
    distances_2_to_1, _ = tree1.query(points2, k=1)
    error_2_to_1 = np.sum(distances_2_to_1**2)
    
    # Combined error
    error_metric = (error_1_to_2 + error_2_to_1) / (len(points1) + len(points2))
    
    return error_metric

In [99]:
error_mesh_penalized = mesh_simplification_error(mesh, mesh_res)

In [100]:
error_mesh_not_penalized = mesh_simplification_error(mesh, mesh_res_no_penalty)

In [101]:
(error_mesh_penalized, error_mesh_not_penalized)

(np.float64(7.317457044963114e-05), np.float64(6.195323090023981e-05))

In [102]:
np.min([error_mesh_penalized, error_mesh_not_penalized])

np.float64(6.195323090023981e-05)

What if we penalize them more? It seems that now the non-penalized mesh is better, but can we get a better simplification with more of the detailed features preserved?

In [103]:
mesh_res1 = simplify.simplify_obj_penalize_clusters(mesh, cluster_labels, high_detail_clusters, 100)

Loaded 3D model.
Selecting the initial valid to contract pairs is done!
0.00% done with 2353 vertices remaining to be removed.
4.25% done with 2253 vertices remaining to be removed.
8.50% done with 2153 vertices remaining to be removed.
12.75% done with 2053 vertices remaining to be removed.
17.00% done with 1953 vertices remaining to be removed.
21.25% done with 1853 vertices remaining to be removed.
25.50% done with 1753 vertices remaining to be removed.
29.75% done with 1653 vertices remaining to be removed.
34.00% done with 1553 vertices remaining to be removed.
38.25% done with 1453 vertices remaining to be removed.
42.50% done with 1353 vertices remaining to be removed.
46.75% done with 1253 vertices remaining to be removed.
51.00% done with 1153 vertices remaining to be removed.
55.25% done with 1053 vertices remaining to be removed.
59.50% done with 953 vertices remaining to be removed.
63.75% done with 853 vertices remaining to be removed.
68.00% done with 753 vertices remaini

In [104]:
mesh_res1.show()

In [105]:
error_mesh_penalized1 = mesh_simplification_error(mesh, mesh_res)
error_mesh_penalized1

np.float64(7.241781085063882e-05)

In [106]:
np.min([error_mesh_penalized1, error_mesh_not_penalized])

np.float64(6.195323090023981e-05)

I guess that the reason why the visual fidelity metric shows that the mesh without penalizing the detailed clusters is better is due to the fact that other parts of the mesh have been badly injured by the simplification process. This simplification algorithm in particular seems to very much depend on the way the quadrics are calculated and the cost of contraction. Maybe it isn't the best way to penalize highly detailed clusters by multiplying all the quadric matrices of vertices having a face in these clusters by a constant? Or maybe in general this specific algorithm is not good when there are interference in general?

## Conclusion

I think there needs a lot more work to be done not only for open questions like:
1. Try other algorithms like DBSCAN, Agglomerative Clustering, etc. but not with the affinity matrix proposed by the paper, but designing featuures w.r.t. the algorithms understanding.
2. A method/heuristic to understand how many clusters can a mesh be divided in?
3. A good heuristic for choosing highly detailed clusters.
4. Improve on the current simplification algorithm and try others with a penalty if they try to simplify clusters which are highly detailed and meant to be preserved? This one is a maybe because most modern algorithms take into consideration such regions of the mesh and try to preserve them as best as they can.

In summary, I wouldn't say my trials were successful or that they are a complete failure. I learned a lot from the paper and the documentations I have read of everything I used.